In [ ]:
import os, re, warnings
warnings.filterwarnings("ignore")

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestClassifier

from mlxtend.frequent_patterns import apriori, association_rules
import statsmodels.api as sm

pd.set_option("display.float_format", lambda x: f"{x:,.2f}")

DATA_DIR = "./data"  # <-- change if needed

# Convenience: short date helpers
def to_month_start(s):
    # Assuming the year is 2019 for the discount data
    return pd.to_datetime(s.astype(str) + ', 2019', errors='coerce').dt.to_period("M").dt.to_timestamp()

def to_date(s):
    return pd.to_datetime(s, errors="coerce")

def safe_pct_to_decimal(s):
    """
    Accepts numbers (like 0.10 or 10) or strings ('10', '10%', '0.10').
    Returns decimal fraction (e.g., 0.10).
    """
    if isinstance(s, pd.Series):
        out = s.copy()
        if out.dtype == object:
            out = out.str.replace('%','', regex=False).str.strip()
        out = pd.to_numeric(out, errors="coerce")
    else:
        # scalar
        if isinstance(s, str):
            s = s.replace("%","").strip()
        out = pd.to_numeric(s, errors="coerce")
    # convert 10 to 0.10, but keep 0.10 as 0.10
    return np.where(out>1, out/100.0, out)

def infer_col(df, candidates, required=True):
    """
    Find a column by list of candidate names (case/underscore/space-insensitive).
    Raises KeyError if required and not found.
    """
    norm = {re.sub(r'[^a-z0-9]', '', c.lower()): c for c in df.columns}
    for cand in candidates:
        key = re.sub(r'[^a-z0-9]', '', cand.lower())
        for k,v in norm.items():
            if k == key:
                return v
    # also try contains
    for cand in candidates:
        key = re.sub(r'[^a-z0-9]', '', cand.lower())
        for k,v in norm.items():
            if key in k:
                return v
    if required:
        raise KeyError(f"Could not find any of {candidates} in columns: {list(df.columns)}")
    return None

def load_csv(name):
    path = os.path.join(DATA_DIR, name)
    if not os.path.exists(path):
        raise FileNotFoundError(f"Expected file not found: {path}")
    return pd.read_csv(path)

sales    = load_csv("/content/Online_Sales.csv")
cust     = load_csv("/content/CustomersData.csv")
disc     = load_csv("/content/Discount_Coupon.csv")
mkt      = load_csv("/content/Marketing_Spend.csv")
tax      = load_csv("/content/Tax_amount.csv")


col_customer   = infer_col(sales, ["CustomerID","Customer_ID"])
col_txn_id     = infer_col(sales, ["Transaction_ID","InvoiceNo","Order_ID"])
col_txn_date   = infer_col(sales, ["Transaction_Date","InvoiceDate","Order_Date"])
col_sku        = infer_col(sales, ["Product_SKU","SKU","Item_ID"], required=False)
col_pdesc      = infer_col(sales, ["Product_Description","Description","Item_Description"], required=False)
col_pcat       = infer_col(sales, ["Product_Category","Product_Cateogry","Category"])
col_qty        = infer_col(sales, ["Quantity","Qty"])
col_price      = infer_col(sales, ["Avg_Price","Unit_Price","Price"])
col_dcharges   = infer_col(sales, ["Delivery_Charges","DeliveryCharges","Shipping","Shipping_Charges"])
col_couponstat = infer_col(sales, ["Coupon_Status","CouponStatus","Coupon_Used"], required=False)

# Discount_Coupon
disc_month = infer_col(disc, ["Month"], required=True)
disc_cat   = infer_col(disc, ["Product_Category","Category"], required=True)
disc_code  = infer_col(disc, ["Coupon_Code"], required=False)
disc_pct   = infer_col(disc, ["Discount_pct","Discount","DiscountPercent"], required=True)

# Tax_Amount
tax_cat = infer_col(tax, ["Product_Category","Category"], required=True)
tax_gst = infer_col(tax, ["GST","Tax","Tax_Rate"], required=True)

# Marketing_Spend
mkt_date   = infer_col(mkt, ["Date"])
mkt_offline= infer_col(mkt, ["Offline_Spend","Offline","TV_Radio_Print"], required=True)
mkt_online = infer_col(mkt, ["Online_Spend","Online","Digital"], required=True)

# Customers
cust_id   = infer_col(cust, ["CustomerID","Customer_ID"])
cust_gender = infer_col(cust, ["Gender"], required=False)
cust_loc    = infer_col(cust, ["Location","City","Region","State"], required=False)
cust_tenure = infer_col(cust, ["Tenure_Months","Tenure","Months_With_Brand"], required=False)

# =========================================
# 2) Cleaning, Types, and Enrichment
# =========================================
# Parse dates
sales[col_txn_date] = to_date(sales[col_txn_date])
disc[disc_month]    = to_month_start(disc[disc_month])
mkt[mkt_date]       = to_date(mkt[mkt_date])

# Fix numeric types
for c in [col_qty, col_price, col_dcharges]:
    sales[c] = pd.to_numeric(sales[c], errors="coerce")

disc[disc_pct] = safe_pct_to_decimal(disc[disc_pct])
tax[tax_gst]   = safe_pct_to_decimal(tax[tax_gst])

sales[col_dcharges] = sales[col_dcharges].fillna(0)
disc[disc_pct]      = disc[disc_pct].fillna(0)
tax[tax_gst]        = tax[tax_gst].fillna(0)

# Build keys
sales["order_month"] = to_month_start(sales[col_txn_date])
disc  = disc.rename(columns={disc_cat: "Product_Category_key", disc_month:"order_month"})
tax   = tax.rename(columns={tax_cat: "Product_Category_key"})
sales = sales.rename(columns={col_pcat:"Product_Category_key"})





/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)


In [ ]:
# Merge Discount by (month, category)
sales = sales.merge(
    disc[["Product_Category_key","order_month", disc_pct]].drop_duplicates(),
    on=["Product_Category_key","order_month"], how="left"
)

# If Coupon_Status present & NOT used, set discount 0; else keep
if col_couponstat and col_couponstat in sales.columns:
    used_mask = sales[col_couponstat].astype(str).str.lower().isin(["used","yes","true","1"])
    sales[disc_pct] = np.where(used_mask, sales[disc_pct].fillna(0), 0.0)
else:
    # If no coupon status, assume discount applies (or 0 if NaN)
    sales[disc_pct] = sales[disc_pct].fillna(0)

# Merge GST by category
sales = sales.merge(
    tax[["Product_Category_key", tax_gst]].drop_duplicates(),
    on="Product_Category_key", how="left"
)
sales[tax_gst] = sales[tax_gst].fillna(0)

# =========================================
# 3) Compute Invoice Value (line-item level)
# =========================================
# Ensure decimals for disc and gst
sales["_disc"] = safe_pct_to_decimal(sales[disc_pct])
sales["_gst"]  = safe_pct_to_decimal(sales[tax_gst])
sales["_qty_price"] = sales[col_qty] * sales[col_price]
sales["_pre_tax_after_disc"] = sales["_qty_price"] * (1 - sales["_disc"])
sales["Tax_Amount_Line"]     = sales["_pre_tax_after_disc"] * sales["_gst"]
sales["Invoice_Value"]       = sales["_pre_tax_after_disc"] * (1 + sales["_gst"]) + sales[col_dcharges]

# Helpful line-level columns
sales["Year"]      = sales[col_txn_date].dt.year
sales["Month"]     = sales[col_txn_date].dt.month
sales["Week"]      = sales[col_txn_date].dt.isocalendar().week.astype(int)
sales["Day"]       = sales[col_txn_date].dt.day
sales["DayName"]   = sales[col_txn_date].dt.day_name()
sales["DOW"]       = sales[col_txn_date].dt.weekday  # 0=Mon
sales["is_weekend"]= sales["DOW"].isin([5,6])

# Attach customer demographics
sales = sales.merge(
    cust[[cust_id] + [c for c in [cust_gender, cust_loc, cust_tenure] if c]],
    left_on=col_customer, right_on=cust_id, how="left"
)

# =========================================
# 4) EDA / Acquisition / Retention / Revenues (new vs existing)
# =========================================
# First purchase month
first_purchase = sales.groupby(col_customer)[col_txn_date].min().rename("first_date")
first_purchase_month = to_month_start(first_purchase).rename("acq_month")
cust_first = pd.concat([first_purchase, first_purchase_month], axis=1)
sales = sales.merge(cust_first, left_on=col_customer, right_index=True, how="left")

# 4.1 Customers acquired every month
acquired_monthly = cust_first["acq_month"].value_counts().sort_index().rename("new_customers").to_frame()
print("\n[Acquisition] Customers acquired each month:\n", acquired_monthly.head())

# 4.2 Month-on-Month retention
sales["active_month"] = sales["order_month"]
cohort_sizes = sales.groupby("acq_month")[col_customer].nunique().rename("cohort_size")
cohort_data  = sales.groupby(["acq_month","active_month"])[col_customer].nunique().reset_index()
cohort_data  = cohort_data.merge(cohort_sizes, on="acq_month", how="left")
cohort_data["retention"] = cohort_data[col_customer] / cohort_data["cohort_size"]
retention_matrix = cohort_data.pivot(index="acq_month", columns="active_month", values="retention").fillna(0)
print("\n[Retention] Retention matrix (rows=cohort month, cols=active month):\n", retention_matrix.iloc[:5,:5])

# Best retention cohort (max mean retention over 6 months)
ret_summary = retention_matrix.iloc[:, :6].mean(axis=1).sort_values(ascending=False)
best_cohort = ret_summary.index[0]
print(f"\n[Retention] Best cohort (avg retention first 6 months): {best_cohort.date()} → {ret_summary.iloc[0]:.2%}")


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Acquisition] Customers acquired each month:
             new_customers
acq_month                
2019-01-01            215
2019-02-01             96
2019-03-01            177
2019-04-01            163
2019-05-01            112

[Retention] Retention matrix (rows=cohort month, cols=active month):
 active_month  2019-01-01  2019-02-01  2019-03-01  2019-04-01  2019-05-01
acq_month                                                               
2019-01-01          1.00        0.06        0.11        0.16        0.11
2019-02-01          0.00        1.00        0.07        0.09        0.17
2019-03-01          0.00        0.00        1.00        0.10        0.20
2019-04-01          0.00        0.00        0.00        1.00        0.09
2019-05-01          0.00        0.00        0.00        0.00        1.00

[Retention] Best cohort (avg retention first 6 months): 2019-01-01 → 27.36%


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 4.3 Revenues from existing vs new customers MoM
sales["is_new_in_month"] = sales["order_month"].eq(sales["acq_month"])
rev_monthly = (sales
               .groupby(["order_month","is_new_in_month"])["Invoice_Value"]
               .sum()
               .reset_index())
rev_pivot = rev_monthly.pivot(index="order_month", columns="is_new_in_month", values="Invoice_Value").fillna(0)
rev_pivot = rev_pivot.rename(columns={True:"Revenue_New", False:"Revenue_Existing"})
rev_pivot["Revenue_Total"] = rev_pivot.sum(axis=1)
print("\n[Revenue] New vs Existing Revenue by month:\n", rev_pivot.head())


[Revenue] New vs Existing Revenue by month:
 is_new_in_month  Revenue_Existing  Revenue_New  Revenue_Total
order_month                                                  
2019-01-01                   0.00   494,090.55     494,090.55
2019-02-01              46,524.59   328,637.45     375,162.05
2019-03-01              68,930.24   346,227.55     415,157.79
2019-04-01             195,985.89   281,512.70     477,498.59
2019-05-01             132,338.75   233,257.28     365,596.03


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 4.4 How discounts play a role in revenues
sales["Discount_Bucket"] = pd.cut(sales["_disc"], bins=[-0.001,0,0.10,0.20,1.0], labels=["0%","0-10%","10-20%","20%+"])
disc_rev = sales.groupby("Discount_Bucket")["Invoice_Value"].agg(["sum","mean","count"]).rename(
    columns={"sum":"Revenue","mean":"Avg_Invoice","count":"Lines"})
disc_rev["Revenue_Share"] = disc_rev["Revenue"]/disc_rev["Revenue"].sum()
print("\n[Discount Impact] Revenue by discount bucket:\n", disc_rev)


[Discount Impact] Revenue by discount bucket:
                      Revenue  Avg_Invoice  Lines  Revenue_Share
Discount_Bucket                                                
0%              3,834,921.69       109.11  35146           0.71
0-10%             584,948.90        98.59   5933           0.11
10-20%            512,685.08        85.45   6000           0.09
20%+              464,803.08        79.52   5845           0.09


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 4.5 KPI by time / category / day
def kpi_by(group_cols):
    g = sales.groupby(group_cols)
    out = pd.DataFrame({
        "Revenue": g["Invoice_Value"].sum(),
        "Orders" : g[col_txn_id].nunique(),
        "Avg_Order_Value": g["Invoice_Value"].sum()/g[col_txn_id].nunique(),
        "Customers": g[col_customer].nunique(),
        "Quantity": g[col_qty].sum()
    }).reset_index()
    return out

kpi_by_month    = kpi_by(["order_month"])
kpi_by_category = kpi_by(["Product_Category_key"])
kpi_by_week     = kpi_by([ "Year","Week"])
kpi_by_dayname  = kpi_by(["DayName"])
kpi_by_loc      = kpi_by([cust_loc]) if cust_loc in sales.columns else None

print("\n[KPI] By month (head):\n", kpi_by_month.head())


[KPI] By month (head):
   order_month    Revenue  Orders  Avg_Order_Value  Customers  Quantity
0  2019-01-01 494,090.55    2102           235.06        215     20140
1  2019-02-01 375,162.05    1664           225.46        109     16575
2  2019-03-01 415,157.79    1991           208.52        208     20787
3  2019-04-01 477,498.59    1813           263.37        224     25277
4  2019-05-01 365,596.03    2034           179.74        200     18715


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 4.6 Trends/seasonality by category, location, month (tables you can plot)
trend_cat_month = sales.pivot_table(index="order_month", columns="Product_Category_key",
                                    values="Invoice_Value", aggfunc="sum").fillna(0)
print("\n[Trends] Revenue by category x month (head):\n", trend_cat_month.head())

# 4.7 Orders & sales by day of week
dow = (sales.groupby("DayName")["Invoice_Value"].agg(["sum","mean","count"])
       .rename(columns={"sum":"Revenue","mean":"Avg_LineValue","count":"Lines"})
       .reindex(["Monday","Tuesday","Wednesday","Thursday","Friday","Saturday","Sunday"]))
print("\n[Day-of-Week] Revenue/Avg line value/Lines:\n", dow)

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Trends] Revenue by category x month (head):
 Product_Category_key  Accessories  Android    Apparel  Backpacks      Bags  \
order_month                                                                  
2019-01-01                  63.23   103.13  59,198.56     336.03 15,655.28   
2019-02-01                   0.00    28.49  55,229.69     662.21 24,630.57   
2019-03-01                  72.49   248.54  80,554.63     802.21 18,486.28   
2019-04-01                 203.16    54.78 114,793.02   1,292.94 14,762.74   
2019-05-01                 180.01   131.15  80,787.47   1,703.00 12,651.92   

Product_Category_key  Bottles  Drinkware      Fun  Gift Cards   Google  \
order_month                                                              
2019-01-01           1,097.45  21,144.00   450.33      276.21 1,314.95   
2019-02-01             582.99  21,091.05   513.52      393.75 1,843.49   
2019-03-01             698.31  30,574.24 1,015.02      378.00 3,342.68   
2019-04-01             757.05  34,57

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 5) Monthly: Revenue, Marketing Spend, % of Revenue, Tax, % Delivery Charges
# =========================================
mkt["order_month"] = to_month_start(mkt[mkt_date])
mkt["Marketing_Spend"] = mkt[mkt_offline].fillna(0) + mkt[mkt_online].fillna(0)
mkt_month = mkt.groupby("order_month")["Marketing_Spend"].sum().to_frame()

tax_month = (sales.groupby("order_month")["Tax_Amount_Line"].sum().to_frame())
deliv_month = (sales.groupby("order_month")[col_dcharges].sum().to_frame().rename(columns={col_dcharges:"Delivery_Charges_Sum"}))
rev_month  = (sales.groupby("order_month")["Invoice_Value"].sum().to_frame().rename(columns={"Invoice_Value":"Revenue"}))

mm = rev_month.join([mkt_month, tax_month, deliv_month], how="left").fillna(0)
mm["Marketing_pct_of_Revenue"] = np.where(mm["Revenue"]>0, mm["Marketing_Spend"]/mm["Revenue"], 0)
mm["Delivery_pct_of_Revenue"]  = np.where(mm["Revenue"]>0, mm["Delivery_Charges_Sum"]/mm["Revenue"], 0)
print("\n[Monthly Financials] Revenue/Marketing/Tax/Delivery and % shares:\n", mm.head())


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Monthly Financials] Revenue/Marketing/Tax/Delivery and % shares:
                Revenue  Marketing_Spend  Tax_Amount_Line  \
order_month                                                
2019-01-01  494,090.55       154,928.95        44,195.47   
2019-02-01  375,162.05       137,107.92        34,548.98   
2019-03-01  415,157.79       122,250.09        38,716.32   
2019-04-01  477,498.59       157,026.83        47,838.83   
2019-05-01  365,596.03       118,259.64        35,325.75   

             Delivery_Charges_Sum  Marketing_pct_of_Revenue  \
order_month                                                   
2019-01-01              59,242.32                      0.31   
2019-02-01              49,216.60                      0.37   
2019-03-01              60,799.94                      0.29   
2019-04-01              41,481.74                      0.33   
2019-05-01              41,396.17                      0.32   

             Delivery_pct_of_Revenue  
order_month                   

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 5.1 Marketing impact on revenue (simple OLS over months)
ols_df = mm.reset_index().dropna()
X = sm.add_constant(ols_df[["Marketing_Spend"]])  # simple model; extend if needed
y = ols_df["Revenue"]
model = sm.OLS(y, X).fit()
print("\n[Marketing Impact → Revenue] OLS summary (Revenue ~ Marketing_Spend):\n", model.summary())

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Marketing Impact → Revenue] OLS summary (Revenue ~ Marketing_Spend):
                             OLS Regression Results                            
Dep. Variable:                Revenue   R-squared:                       0.634
Model:                            OLS   Adj. R-squared:                  0.597
Method:                 Least Squares   F-statistic:                     17.33
Date:                Tue, 02 Sep 2025   Prob (F-statistic):            0.00194
Time:                        02:47:08   Log-Likelihood:                -143.88
No. Observations:                  12   AIC:                             291.8
Df Residuals:                      10   BIC:                             292.7
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                      coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 6) Products: appearance & most purchased by quantity
# =========================================
if col_sku:
    prod_appear = sales[col_sku].nunique()
else:
    prod_appear = sales["Product_Category_key"].nunique()

top_qty = (sales.groupby(col_pdesc if col_pdesc else "Product_Category_key")[col_qty]
           .sum().sort_values(ascending=False).head(10))
print(f"\n[Products] Unique items/categories appeared: {prod_appear}")
print("\n[Products] Top-10 by total quantity:\n", top_qty)


[Products] Unique items/categories appeared: 1145

[Products] Top-10 by total quantity:
 Product_Description
Maze Pen                                  16234
Google 22 oz Water Bottle                 14282
Google Sunglasses                         11452
Sport Bag                                  7321
Google Metallic Notebook Set               6496
Google Laptop and Cell Phone Stickers      5847
Google Kick Ball                           5549
Recycled Paper Journal Set                 5381
Nest Cam Outdoor Security Camera - USA     5206
Foam Can and Bottle Cooler                 5098
Name: Quantity, dtype: int64


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 7) Customer Segmentation — Value Bands & RFM & K-Means
# =========================================
snapshot_date = sales[col_txn_date].max() + pd.Timedelta(days=1)

rfm = (sales.groupby(col_customer)
       .agg(RecencyDays = (col_txn_date, lambda s: (snapshot_date - s.max()).days),
            Frequency  = (col_txn_id, "nunique"),
            Monetary   = ("Invoice_Value", "sum"))
       .reset_index())

# Value bands based on Monetary tertiles
q = rfm["Monetary"].quantile([0.33,0.66]).values
def value_band(x):
    if x<=q[0]: return "Standard"
    if x<=q[1]: return "Silver"
    return "Gold/Premium"
rfm["Value_Band"] = rfm["Monetary"].apply(value_band)

# RFM Score (1 low .. 4 high per quartiles)
r_labels = [4,3,2,1]  # lower recency is better
f_labels = [1,2,3,4]
m_labels = [1,2,3,4]
rfm["R_Score"] = pd.qcut(rfm["RecencyDays"], 4, labels=r_labels)
rfm["F_Score"] = pd.qcut(rfm["Frequency"],   4, labels=f_labels)
rfm["M_Score"] = pd.qcut(rfm["Monetary"],    4, labels=m_labels)
rfm["RFM_Sum"] = rfm[["R_Score","F_Score","M_Score"]].astype(int).sum(axis=1)

def rfm_segment(score):
    if score>=10: return "Premium"
    if score>=8:  return "Gold"
    if score>=6:  return "Silver"
    return "Standard"
rfm["RFM_Segment"] = rfm["RFM_Sum"].apply(rfm_segment)

print("\n[Segmentation] RFM segments (counts):\n", rfm["RFM_Segment"].value_counts())

# K-Means on scaled RFM
X_km = rfm[["RecencyDays","Frequency","Monetary"]].copy()
X_km["Monetary"] = np.log1p(X_km["Monetary"])
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_km)

kmeans = KMeans(n_clusters=4, random_state=42, n_init="auto")
rfm["KMeans_Segment"] = kmeans.fit_predict(X_scaled)
print("\n[Segmentation] K-Means cluster sizes:\n", rfm["KMeans_Segment"].value_counts().sort_index())

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Segmentation] RFM segments (counts):
 RFM_Segment
Standard    422
Premium     404
Silver      336
Gold        306
Name: count, dtype: int64


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)



[Segmentation] K-Means cluster sizes:
 KMeans_Segment
0    316
1    414
2     54
3    684
Name: count, dtype: int64


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 8) Predicting CLV Class (Low/Med/High) — Classification
# =========================================
# Feature assembly at customer-level
cust_feat = (sales
    .groupby(col_customer)
    .agg(
        Total_Revenue=("Invoice_Value","sum"),
        Orders=(col_txn_id,"nunique"),
        First_Date=(col_txn_date,"min"),
        Last_Date=(col_txn_date,"max"),
        Avg_Discount=("_disc","mean"),
        Avg_GST=("_gst","mean"),
        Avg_Qty=(col_qty,"mean"),
        Avg_Price=(col_price,"mean"),
        Delivery_Share=(col_dcharges, lambda s: s.sum()),
    )
    .reset_index()
)
cust_feat["Days_Since_Last"] = (snapshot_date - cust_feat["Last_Date"]).dt.days
cust_feat["Tenure_Days"] = (cust_feat["Last_Date"] - cust_feat["First_Date"]).dt.days.clip(lower=0)
cust_feat["AOV"] = cust_feat["Total_Revenue"]/cust_feat["Orders"].replace(0, np.nan)

# Target: tertiles of Total_Revenue → Low/Medium/High
t = cust_feat["Total_Revenue"].quantile([0.33,0.66]).values
def clv_band(v):
    if v<=t[0]: return "Low"
    if v<=t[1]: return "Medium"
    return "High"
cust_feat["CLV_Class"] = cust_feat["Total_Revenue"].apply(clv_band)

# Model features
feature_cols = ["Orders","Days_Since_Last","Tenure_Days","Avg_Discount","Avg_GST","Avg_Qty","Avg_Price","AOV"]
X = cust_feat[feature_cols].fillna(0)
y = cust_feat["CLV_Class"]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=42, stratify=y)
clf = RandomForestClassifier(n_estimators=300, random_state=42, class_weight="balanced")
clf.fit(X_train, y_train)
y_pred = clf.predict(X_test)

print("\n[CLV Classification] Report:\n", classification_report(y_test, y_pred))
print("\nConfusion Matrix:\n", pd.DataFrame(confusion_matrix(y_test, y_pred),
      index=[f"true_{c}" for c in clf.classes_], columns=[f"pred_{c}" for c in clf.classes_]))

fi = pd.Series(clf.feature_importances_, index=feature_cols).sort_values(ascending=False)
print("\n[CLV Classification] Feature importances:\n", fi)

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[CLV Classification] Report:
               precision    recall  f1-score   support

        High       0.98      0.92      0.95       125
         Low       0.94      0.96      0.95       121
      Medium       0.89      0.93      0.91       121

    accuracy                           0.93       367
   macro avg       0.94      0.93      0.93       367
weighted avg       0.94      0.93      0.93       367


Confusion Matrix:
              pred_High  pred_Low  pred_Medium
true_High          115         1            9
true_Low             0       116            5
true_Medium          2         7          112

[CLV Classification] Feature importances:
 Orders            0.45
AOV               0.20
Avg_Price         0.08
Avg_Qty           0.08
Tenure_Days       0.05
Avg_GST           0.05
Avg_Discount      0.05
Days_Since_Last   0.03
dtype: float64


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 9) Cross-Selling — Market Basket Analysis (Apriori)
# =========================================
# We'll use Transaction_ID × Product_Category to keep sparse matrix small.
basket = (sales
          .groupby([col_txn_id,"Product_Category_key"])
          .size().unstack(fill_value=0))
basket = basket.applymap(lambda x: 1 if x>0 else 0)
freq_items = apriori(basket, min_support=0.02, use_colnames=True)
rules = association_rules(freq_items, metric="lift", min_threshold=1.0)
rules = rules.sort_values(["confidence","lift"], ascending=False)
print("\n[Cross-Sell] Top association rules (head):\n", rules.head(10)[["antecedents","consequents","support","confidence","lift"]])

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Cross-Sell] Top association rules (head):
              antecedents  consequents  support  confidence  lift
16           (Lifestyle)     (Office)     0.04        0.51  3.65
4            (Lifestyle)    (Apparel)     0.03        0.48  1.49
14           (Drinkware)     (Office)     0.05        0.46  3.27
18  (Apparel, Drinkware)     (Office)     0.02        0.46  3.26
3            (Drinkware)    (Apparel)     0.05        0.45  1.38
20   (Drinkware, Office)    (Apparel)     0.02        0.45  1.38
7               (Office)    (Apparel)     0.06        0.44  1.36
10                (Bags)     (Office)     0.03        0.43  3.04
0                 (Bags)    (Apparel)     0.03        0.42  1.28
12           (Lifestyle)  (Drinkware)     0.03        0.38  3.76


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/mlxtend/frequent_patterns/fpcommon.py:161: DeprecationWarning: DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: Dep

In [ ]:
# 10) Predicting Next Purchase Window — Classification
# =========================================
# Interpurchase times per repeat customer
txn_order = (sales[[col_customer, col_txn_id, col_txn_date]]
             .drop_duplicates()
             .sort_values([col_customer, col_txn_date]))
txn_order["Prev_Date"] = txn_order.groupby(col_customer)[col_txn_date].shift(1)
txn_order["Delta_Days"] = (txn_order[col_txn_date] - txn_order["Prev_Date"]).dt.days

avg_delta = (txn_order
             .dropna(subset=["Delta_Days"])
             .groupby(col_customer)["Delta_Days"]
             .mean()
             .rename("Avg_Days_Between"))
avg_delta = avg_delta[avg_delta>0].to_frame()

def next_window(d):
    if d<=30: return "0-30"
    if d<=60: return "30-60"
    if d<=90: return "60-90"
    return "90+"

avg_delta["Next_Window"] = avg_delta["Avg_Days_Between"].apply(next_window)

# Join to RFM-like features for classification
np_feat = rfm.set_index(col_customer).join(avg_delta, how="inner").reset_index()
np_feat = np_feat.merge(cust_feat[[col_customer,"Orders","AOV","Avg_Discount","Avg_GST"]], on=col_customer, how="left")

X2 = np_feat[["RecencyDays","Frequency","Monetary","Orders","AOV","Avg_Discount","Avg_GST"]].copy()
X2[["Monetary","AOV"]] = np.log1p(X2[["Monetary","AOV"]])
y2 = np_feat["Next_Window"]

X2_train, X2_test, y2_train, y2_test = train_test_split(X2.fillna(0), y2, test_size=0.25, random_state=42, stratify=y2)
clf2 = RandomForestClassifier(n_estimators=300, random_state=42, class_weight="balanced")
clf2.fit(X2_train, y2_train)
y2_pred = clf2.predict(X2_test)
print("\n[Next Purchase Window] Report:\n", classification_report(y2_test, y2_pred))
print("\nConfusion Matrix:\n", pd.DataFrame(confusion_matrix(y2_test, y2_pred),
      index=[f"true_{c}" for c in clf2.classes_], columns=[f"pred_{c}" for c in clf2.classes_]))

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag


[Next Purchase Window] Report:
               precision    recall  f1-score   support

        0-30       0.96      0.98      0.97       171
       30-60       0.00      0.00      0.00         8
       60-90       0.00      0.00      0.00         3
         90+       0.33      1.00      0.50         2

    accuracy                           0.92       184
   macro avg       0.32      0.50      0.37       184
weighted avg       0.90      0.92      0.91       184


Confusion Matrix:
             pred_0-30  pred_30-60  pred_60-90  pred_90+
true_0-30         168           0           1         2
true_30-60          6           0           0         2
true_60-90          1           2           0         0
true_90+            0           0           0         2


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# 11) Cohort analysis — behavior by start month & maximum retention
# (already computed retention_matrix above)
cohort_counts = (sales.groupby(["acq_month","active_month"])[col_customer]
                 .nunique().reset_index(name="actives"))
cohort_pivot = cohort_counts.pivot(index="acq_month", columns="active_month", values="actives").fillna(0)
cohort_pivot = cohort_pivot.div(cohort_pivot.iloc[:,0], axis=0)  # normalize by cohort size in month 0
cohort_month_ret = cohort_pivot.mean(axis=1).sort_values(ascending=False)
best_cohort2 = cohort_month_ret.index[0]
print(f"\n[Cohort] Highest average retention cohort: {best_cohort2.date()} (avg retention across periods = {cohort_month_ret.iloc[0]:.2%})")

print("\nAll steps complete ✅")


[Cohort] Highest average retention cohort: 2019-02-01 (avg retention across periods = inf%)

All steps complete ✅


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

In [ ]:
# ================================
# Monthly Retention Bar Chart (with Δ vs previous month)
# Definition: For month m, retention = |customers active in m-1 AND m| / |customers active in m-1|
# ================================
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = "plotly_white"

def _find_col(df, candidates, required=True):
    norm = {"".join(filter(str.isalnum, c.lower())): c for c in df.columns}
    for cand in candidates:
        key = "".join(filter(str.isalnum, cand.lower()))
        if key in norm:
            return norm[key]
    for cand in candidates:  # soft contains
        key = "".join(filter(str.isalnum, cand.lower()))
        for k, v in norm.items():
            if key in k:
                return v
    if required:
        raise KeyError(f"Could not find any of {candidates} in columns: {list(df.columns)}")
    return None

# --- Resolve columns & month key ---
cid = _find_col(sales, ["CustomerID","Customer_ID"])
tdt = _find_col(sales, ["Transaction_Date","Order_Date","InvoiceDate"])

sales = sales.copy()
sales[tdt] = pd.to_datetime(sales[tdt], errors="coerce")
if "order_month" not in sales.columns:
    sales["order_month"] = sales[tdt].dt.to_period("M").dt.to_timestamp()

# --- Build month -> set(customers) map ---
months = np.sort(sales["order_month"].dropna().unique())
month_sets = {m: set(sales.loc[sales["order_month"] == m, cid]) for m in months}

# --- Compute rolling month-to-month retention ---
ret_values = []
for i, m in enumerate(months):
    if i == 0:
        ret = np.nan  # no previous month
    else:
        prev = months[i-1]
        prev_set, cur_set = month_sets[prev], month_sets[m]
        denom = len(prev_set)
        ret = (len(prev_set & cur_set) / denom) if denom > 0 else np.nan
    ret_values.append(ret)

ret_df = pd.DataFrame({"order_month": months, "Retention": ret_values})
ret_df["Retention_pct"] = ret_df["Retention"] * 100
# % change vs previous month’s retention (not percentage points)
ret_df["Retention_change_pct"] = ret_df["Retention"].pct_change()  # fractional change
ret_df["Delta_label"] = ret_df["Retention_change_pct"].apply(
    lambda x: "—" if pd.isna(x) or np.isinf(x) else f"{x*100:+.1f}%"
)

# --- Bar colors: green for ↑, red for ↓, grey for first month/NaN ---
colors = np.where(ret_df["Retention_change_pct"].fillna(0) > 0, "#2ca02c",
          np.where(ret_df["Retention_change_pct"].fillna(0) < 0, "#d62728", "#9ca3af"))

# Hide the first bar (no retention definition) but keep it on X for continuity
y_vals = ret_df["Retention_pct"].astype(float).tolist()
if len(y_vals) > 0:
    y_vals[0] = None  # leaves a gap for month 0

# --- Plotly bar with labels showing Δ vs previous month ---
fig = go.Figure(go.Bar(
    x=ret_df["order_month"],
    y=y_vals,
    marker_color=colors,
    text=ret_df["Delta_label"],
    textposition="outside",
    hovertemplate="<b>%{x|%b %Y}</b><br>Retention: %{y:.1f}%<br>Δ vs prev: %{text}<extra></extra>"
))

# Optional reference lines: mean & median (computed on valid months only)
valid = ret_df["Retention_pct"].dropna()
if len(valid) > 0:
    fig.add_hline(y=valid.mean(), line_dash="dot", line_color="#636EFA",
                  annotation_text=f"Mean: {valid.mean():.1f}%", annotation_position="top left")
    fig.add_hline(y=valid.median(), line_dash="dash", line_color="#00CC96",
                  annotation_text=f"Median: {valid.median():.1f}%", annotation_position="bottom left")

# Layout
upper = (np.nanmax(valid) if len(valid) else 0) * 1.15
upper = 100 if (upper == 0 or np.isnan(upper)) else upper
fig.update_layout(
    title="Monthly Customer Retention (Rolling) — % of Last Month’s Customers Returning",
    xaxis_title="Month",
    yaxis_title="Retention (%)",
    xaxis=dict(tickformat="%b %Y"),
    yaxis=dict(range=[0, upper]),
    height=520,
    margin=dict(l=70, r=20, t=70, b=60)
)
# ---- Force every month label on the x-axis ----
months_sorted = ret_df["order_month"].sort_values().unique()

fig.update_xaxes(
    tickmode="array",
    tickvals=months_sorted,                                   # one tick per bar
    ticktext=[pd.to_datetime(m).strftime("%b %Y") for m in months_sorted],
    tickangle=-45                                             # tilt to prevent collisions
)

# optional polish (helps when there are many months):
fig.update_layout(xaxis=dict(tickfont=dict(size=10), automargin=True))

fig.show()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  return datetime.utcnow().replace(tzinfo=utc)
/usr/local/lib/python3.12/dist-packag

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
# Q5) New vs Existing Revenue by Month (stacked) + Total line
# =========================================
# Define 'inv' within this cell for robustness
from plotly.subplots import make_subplots

inv = "Invoice_Value"

rev_mo = (sales.groupby(["order_month","is_new_in_month"])[inv]
          .sum().reset_index())
rev_pivot = rev_mo.pivot(index="order_month", columns="is_new_in_month", values=inv).fillna(0)
rev_pivot = rev_pivot.rename(columns={True:"Revenue_New", False:"Revenue_Existing"})
rev_pivot["Revenue_Total"] = rev_pivot.sum(axis=1)
rev_pivot = rev_pivot.sort_index().reset_index()

fig5 = make_subplots(specs=[[{"secondary_y": True}]])
fig5.add_trace(
    go.Bar(
        x=rev_pivot["order_month"], y=rev_pivot["Revenue_Existing"],
        name="Existing Customers", marker_color="#1f77b4",
        hovertemplate="<b>%{x|%b %Y}</b><br>Existing Revenue: %{y:,.0f}<extra></extra>"
    ),
    secondary_y=False
)
fig5.add_trace(
    go.Bar(
        x=rev_pivot["order_month"], y=rev_pivot["Revenue_New"],
        name="New Customers", marker_color="#ff7f0e",
        hovertemplate="<b>%{x|%b %Y}</b><br>New Revenue: %{y:,.0f}<extra></extra>"
    ),
    secondary_y=False
)
fig5.add_trace(
    go.Scatter(
        x=rev_pivot["order_month"], y=rev_pivot["Revenue_Total"],
        name="Total Revenue", mode="lines+markers", line=dict(width=3),
        hovertemplate="<b>%{x|%b %Y}</b><br>Total Rev: %{y:,.0f}<extra></extra>"
    ),
    secondary_y=True
)
fig5.update_layout(
    barmode="stack",
    title="Q5 • Revenue by Month: New vs Existing (Stacked) + Total Trend",
    xaxis_title="Month",
    yaxis_title="Revenue (Stacked Bars)",
    legend_title="Customer Type",
    height=520
)
fig5.update_xaxes(tickformat="%b %Y")
fig5.update_yaxes(title_text="Revenue (Total Line)", secondary_y=True)
fig5.show()

# Insight tip: If Total line grows while New bar shrinks, loyalty/retention programs are working; if New dominates, acquisition-led growth.

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
# Q7) KPI Dashboard (Monthly): Revenue, Orders, AOV, Unique Customers
# =========================================
# Define inv, tid, cid, and pcat within this cell for robustness
inv = "Invoice_Value"
cid = col_customer
tid = col_txn_id
pcat = "Product_Category_key"

kpi = (sales.groupby("order_month")
       .agg(Revenue=(inv,"sum"),
            Orders=(tid,"nunique"),
            Customers=(cid,"nunique"))
       .reset_index())
kpi["AOV"] = kpi["Revenue"] / kpi["Orders"].replace(0, np.nan)

fig7 = make_subplots(rows=2, cols=2, subplot_titles=(
    "Revenue by Month", "Orders by Month", "AOV by Month", "Unique Customers by Month"
))
fig7.add_trace(go.Scatter(x=kpi["order_month"], y=kpi["Revenue"], mode="lines+markers", name="Revenue",
                          hovertemplate="%{x|%b %Y}<br>Revenue: %{y:,.0f}<extra></extra>"), row=1, col=1)
fig7.add_trace(go.Bar(x=kpi["order_month"], y=kpi["Orders"], name="Orders",
                      hovertemplate="%{x|%b %Y}<br>Orders: %{y:,.0f}<extra></extra>"), row=1, col=2)
fig7.add_trace(go.Scatter(x=kpi["order_month"], y=kpi["AOV"], mode="lines+markers", name="AOV",
                          hovertemplate="%{x|%b %Y}<br>AOV: %{y:,.0f}<extra></extra>"), row=2, col=1)
fig7.add_trace(go.Bar(x=kpi["order_month"], y=kpi["Customers"], name="Customers",
                      hovertemplate="%{x|%b %Y}<br>Customers: %{y:,.0f}<extra></extra>"), row=2, col=2)

fig7.update_layout(height=700, title_text="Q7 • Monthly KPIs")
for ax in ["xaxis","xaxis2","xaxis3","xaxis4"]:
    fig7["layout"][ax].update(tickformat="%b %Y")
fig7.show()

# Insight tip: Use AOV trend against discount mix (#6) to validate promo efficiency without over-subsidizing orders.


# =========================================
# Q8) Seasonality by Category (Category × Month Heatmap)
# =========================================
# Focus top 12 categories by revenue for readability
top_cats = (sales.groupby(pcat)[inv].sum().sort_values(ascending=False).head(12).index)
season = (sales[sales[pcat].isin(top_cats)]
          .groupby(["order_month", pcat])[inv].sum()
          .reset_index())

season_p = season.pivot(index="order_month", columns=pcat, values=inv).fillna(0)
fig8 = go.Figure(
    data=go.Heatmap(
        z=season_p.values,
        x=season_p.columns.astype(str),
        y=[d.strftime("%b %Y") for d in season_p.index],
        colorscale="Tealrose",
        hovertemplate="<b>Month:</b> %{y}<br><b>Category:</b> %{x}<br><b>Revenue:</b> %{z:,.0f}<extra></extra>"
    )
)
fig8.update_layout(
    title="Q8 • Seasonality Heatmap: Revenue by Category × Month (Top 12 Categories)",
    xaxis_title="Product Category",
    yaxis_title="Month",
    height=560
)
fig8.show()

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
import plotly.express as px

bubble = sales.merge(
    sales.groupby("order_month")[inv].sum().rename("Month_Total"),
    on="order_month"
)
bubble["SharePct"] = (bubble[inv] / bubble["Month_Total"].replace(0,np.nan))*100
bubble["Month_lbl"] = bubble["order_month"].dt.strftime("%b %Y")

fig = px.scatter(
    bubble, x=pcat, y="Month_lbl", size=inv, color="SharePct",
    color_continuous_scale="Viridis", range_color=[0,100],
    labels={pcat:"Product Category", "Month_lbl":"Month", inv:"Revenue", "SharePct":"% of Month"},
    title="Bubble Matrix — Revenue (size) & Share of Month (color)"
)
fig.update_traces(
    hovertemplate="<b>%{y}</b><br>%{x}<br>Revenue: %{marker.size:,.0f}<br>Share: %{marker.color:.1f}%<extra></extra>"
)
fig.update_layout(height=650, xaxis_tickangle=-35)
fig.show()

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
# Q11) Marketing Spend → Revenue Impact (Scatter with Fit)
# =========================================
# Use same mm from Q10; compute a simple linear fit and show R²
df = mm.reset_index().copy()
x = df["Marketing_Spend"].values
y = df["Revenue"].values

if (x.std() == 0) or (y.std() == 0):
    # Avoid division by zero / degenerate fit
    slope = intercept = r2 = 0.0
    yhat = y
else:
    slope, intercept = np.polyfit(x, y, 1)
    yhat = slope * x + intercept
    # R² via correlation
    r = np.corrcoef(x, y)[0,1]
    r2 = 0 if np.isnan(r) else r**2

# Bubble size by #Orders in month (adds behavioral context)
orders_m = sales.groupby("order_month")[tid].nunique().rename("Orders").reset_index()
df = df.merge(orders_m, on="order_month", how="left").fillna(0)
size = np.clip((df["Orders"] / (df["Orders"].max() or 1)) * 40 + 10, 10, 60)  # readable bubble sizes

fig11 = go.Figure()
fig11.add_trace(go.Scatter(
    x=df["Marketing_Spend"], y=df["Revenue"],
    mode="markers+text",
    text=[d.strftime("%b %Y") for d in df["order_month"]],
    textposition="top center",
    marker=dict(size=size, line=dict(width=1, color="white")),
    name="Month",
    hovertemplate="<b>%{text}</b><br>Marketing: %{x:,.0f}<br>Revenue: %{y:,.0f}<br>Orders: %{marker.size:.0f}<extra></extra>"
))
fig11.add_trace(go.Scatter(
    x=df["Marketing_Spend"], y=yhat,
    mode="lines", name=f"Fit: y = {slope:,.2f}x + {intercept:,.0f}  |  R² = {r2:.2f}",
    line=dict(width=3, color="#636EFA")
))

fig11.update_layout(
    title="Q11 • Marketing Spend vs Revenue (with Linear Fit & R²)",
    xaxis_title="Marketing Spend (₹)",
    yaxis_title="Revenue (₹)",
    height=540
)
fig11.show()

# Interpretation tip:
# • Positive slope with high R² → spend is strongly associated with revenue (good, but check causality & diminishing returns).
# • Flat/negative slope or low R² → optimize channels/creatives, consider shifting spend to retention or high-ROI months.

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
import os, re, warnings
warnings.filterwarnings("ignore")

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestClassifier

from mlxtend.frequent_patterns import apriori, association_rules
import statsmodels.api as sm

pd.set_option("display.float_format", lambda x: f"{x:,.2f}")

DATA_DIR = "./data"  # <-- change if needed

# Convenience: short date helpers
def to_month_start(s):
    # Assuming the year is 2019 for the discount data
    return pd.to_datetime(s.astype(str) + ', 2019', errors='coerce').dt.to_period("M").dt.to_timestamp()

def to_date(s):
    return pd.to_datetime(s, errors="coerce")

def safe_pct_to_decimal(s):
    """
    Accepts numbers (like 0.10 or 10) or strings ('10', '10%', '0.10').
    Returns decimal fraction (e.g., 0.10).
    """
    if isinstance(s, pd.Series):
        out = s.copy()
        if out.dtype == object:
            out = out.str.replace('%','', regex=False).str.strip()
        out = pd.to_numeric(out, errors="coerce")
    else:
        # scalar
        if isinstance(s, str):
            s = s.replace("%","").strip()
        out = pd.to_numeric(s, errors="coerce")
    # convert 10 to 0.10, but keep 0.10 as 0.10
    return np.where(out>1, out/100.0, out)

def infer_col(df, candidates, required=True):
    """
    Find a column by list of candidate names (case/underscore/space-insensitive).
    Raises KeyError if required and not found.
    """
    norm = {re.sub(r'[^a-z0-9]', '', c.lower()): c for c in df.columns}
    for cand in candidates:
        key = re.sub(r'[^a-z0-9]', '', cand.lower())
        for k,v in norm.items():
            if k == key:
                return v
    # also try contains
    for cand in candidates:
        key = re.sub(r'[^a-z0-9]', '', cand.lower())
        for k,v in norm.items():
            if key in k:
                return v
    if required:
        raise KeyError(f"Could not find any of {candidates} in columns: {list(df.columns)}")
    return None

def load_csv(name):
    path = os.path.join(DATA_DIR, name)
    if not os.path.exists(path):
        raise FileNotFoundError(f"Expected file not found: {path}")
    return pd.read_csv(path)

sales    = load_csv("/content/Online_Sales.csv")
cust     = load_csv("/content/CustomersData.csv")
disc     = load_csv("/content/Discount_Coupon.csv")
mkt      = load_csv("/content/Marketing_Spend.csv")
tax      = load_csv("/content/Tax_amount.csv")


col_customer   = infer_col(sales, ["CustomerID","Customer_ID"])
col_txn_id     = infer_col(sales, ["Transaction_ID","InvoiceNo","Order_ID"])
col_txn_date   = infer_col(sales, ["Transaction_Date","InvoiceDate","Order_Date"])
col_sku        = infer_col(sales, ["Product_SKU","SKU","Item_ID"], required=False)
col_pdesc      = infer_col(sales, ["Product_Description","Description","Item_Description"], required=False)
col_pcat       = infer_col(sales, ["Product_Category","Product_Cateogry","Category"])
col_qty        = infer_col(sales, ["Quantity","Qty"])
col_price      = infer_col(sales, ["Avg_Price","Unit_Price","Price"])
col_dcharges   = infer_col(sales, ["Delivery_Charges","DeliveryCharges","Shipping","Shipping_Charges"])
col_couponstat = infer_col(sales, ["Coupon_Status","CouponStatus","Coupon_Used"], required=False)

# Discount_Coupon
disc_month = infer_col(disc, ["Month"], required=True)
disc_cat   = infer_col(disc, ["Product_Category","Category"], required=True)
disc_code  = infer_col(disc, ["Coupon_Code"], required=False)
disc_pct   = infer_col(disc, ["Discount_pct","Discount","DiscountPercent"], required=True)

# Tax_Amount
tax_cat = infer_col(tax, ["Product_Category","Category"], required=True)
tax_gst = infer_col(tax, ["GST","Tax","Tax_Rate"], required=True)

# Marketing_Spend
mkt_date   = infer_col(mkt, ["Date"])
mkt_offline= infer_col(mkt, ["Offline_Spend","Offline","TV_Radio_Print"], required=True)
mkt_online = infer_col(mkt, ["Online_Spend","Online","Digital"], required=True)

# Customers
cust_id   = infer_col(cust, ["CustomerID","Customer_ID"])
cust_gender = infer_col(cust, ["Gender"], required=False)
cust_loc    = infer_col(cust, ["Location","City","Region","State"], required=False)
cust_tenure = infer_col(cust, ["Tenure_Months","Tenure","Months_With_Brand"], required=False)

# =========================================
# 2) Cleaning, Types, and Enrichment
# =========================================
# Parse dates
sales[col_txn_date] = to_date(sales[col_txn_date])
disc[disc_month]    = to_month_start(disc[disc_month])
mkt[mkt_date]       = to_date(mkt[mkt_date])

# Fix numeric types
for c in [col_qty, col_price, col_dcharges]:
    sales[c] = pd.to_numeric(sales[c], errors="coerce")

disc[disc_pct] = safe_pct_to_decimal(disc[disc_pct])
tax[tax_gst]   = safe_pct_to_decimal(tax[tax_gst])

sales[col_dcharges] = sales[col_dcharges].fillna(0)
disc[disc_pct]      = disc[disc_pct].fillna(0)
tax[tax_gst]        = tax[tax_gst].fillna(0)

# Build keys
sales["order_month"] = to_month_start(sales[col_txn_date])
disc  = disc.rename(columns={disc_cat: "Product_Category_key", disc_month:"order_month"})
tax   = tax.rename(columns={tax_cat: "Product_Category_key"})
sales = sales.rename(columns={col_pcat:"Product_Category_key"})


# Merge Discount by (month, category)
sales = sales.merge(
    disc[["Product_Category_key","order_month", disc_pct]].drop_duplicates(),
    on=["Product_Category_key","order_month"], how="left"
)

# If Coupon_Status present & NOT used, set discount 0; else keep
if col_couponstat and col_couponstat in sales.columns:
    used_mask = sales[col_couponstat].astype(str).str.lower().isin(["used","yes","true","1"])
    sales[disc_pct] = np.where(used_mask, sales[disc_pct].fillna(0), 0.0)
else:
    # If no coupon status, assume discount applies (or 0 if NaN)
    sales[disc_pct] = sales[disc_pct].fillna(0)

# Merge GST by category
sales = sales.merge(
    tax[["Product_Category_key", tax_gst]].drop_duplicates(),
    on="Product_Category_key", how="left"
)
sales[tax_gst] = sales[tax_gst].fillna(0)

# =========================================
# 3) Compute Invoice Value (line-item level)
# =========================================
# Ensure decimals for disc and gst
sales["_disc"] = safe_pct_to_decimal(sales[disc_pct])
sales["_gst"]  = safe_pct_to_decimal(sales[tax_gst])
sales["_qty_price"] = sales[col_qty] * sales[col_price]
sales["_pre_tax_after_disc"] = sales["_qty_price"] * (1 - sales["_disc"])
sales["Tax_Amount_Line"]     = sales["_pre_tax_after_disc"] * sales["_gst"]
sales["Invoice_Value"]       = sales["_pre_tax_after_disc"] * (1 + sales["_gst"]) + sales[col_dcharges]


# --- Recreate mm DataFrame ---
mkt["order_month"] = to_month_start(mkt[mkt_date])
mkt["Marketing_Spend"] = mkt[mkt_offline].fillna(0) + mkt[mkt_online].fillna(0)
mkt_month = mkt.groupby("order_month")["Marketing_Spend"].sum().to_frame()

tax_month = (sales.groupby("order_month")["Tax_Amount_Line"].sum().to_frame())
deliv_month = (sales.groupby("order_month")[col_dcharges].sum().to_frame().rename(columns={col_dcharges:"Delivery_Charges_Sum"}))
rev_month  = (sales.groupby("order_month")["Invoice_Value"].sum().to_frame().rename(columns={"Invoice_Value":"Revenue"}))

mm = rev_month.join([mkt_month, tax_month, deliv_month], how="left").fillna(0)
mm["Marketing_pct_of_Revenue"] = np.where(mm["Revenue"]>0, mm["Marketing_Spend"]/mm["Revenue"], 0)
mm["Delivery_pct_of_Revenue"]  = np.where(mm["Revenue"]>0, mm["Delivery_Charges_Sum"]/mm["Revenue"], 0)
# --- End Recreate mm DataFrame ---


df = mm.copy()

# Reset index to make 'order_month' a column and explicitly name it
df = df.reset_index(names=['order_month'])


df = df.sort_values("order_month") # Use 'order_month' as the column name
base_rev = df["Revenue"].iloc[0] if df.shape[0] else 1
base_mkt = df["Marketing_Spend"].iloc[0] if df.shape[0] else 1
df["Rev_idx"] = np.where(base_rev>0, df["Revenue"]/base_rev*100, np.nan)
df["Mkt_idx"] = np.where(base_mkt>0, df["Marketing_Spend"]/base_mkt*100, np.nan)

fig = go.Figure()
fig.add_hline(y=100, line_dash="dot", line_color="#94A3B8",
              annotation_text="Base = 100", annotation_position="top left")

fig.add_trace(go.Scatter(
    x=df["order_month"], y=df["Rev_idx"], mode="lines+markers",
    name="Revenue (Indexed)", line=dict(width=3, color="#636EFA"),
    hovertemplate="<b>%{x|%b %Y}</b><br>Revenue idx: %{y:.1f}<br>Rev: ₹%{customdata:,.0f}<extra></extra>",
    customdata=df["Revenue"]
))
fig.add_trace(go.Scatter(
    x=df["order_month"], y=df["Mkt_idx"], mode="lines+markers",
    name="Marketing (Indexed)", line=dict(width=3, color="#EF553B"),
    hovertemplate="<b>%{x|%b %Y}</b><br>Marketing idx: %{y:.1f}<br>Mkt: ₹%{customdata:,.0f}<extra></extra>",
    customdata=df["Marketing_Spend"]
))

# annotate last points with values
if df.shape[0]:
    last = df.iloc[-1]
    fig.add_annotation(x=last["order_month"], y=last["Rev_idx"],
                       text=f"Rev {last['Rev_idx']:.0f}", showarrow=False, yshift=12)
    fig.add_annotation(x=last["order_month"], y=last["Mkt_idx"],
                       text=f"Mkt {last['Mkt_idx']:.0f}", showarrow=False, yshift=-12)

fig.update_layout(
    title="Q11 • Indexed Trend — Revenue vs Marketing (Base = 100)",
    xaxis_title="Month", yaxis_title="Index (Base Month = 100)",
    height=520, legend_title=""
)
# force every month label
months_sorted = df["order_month"].unique() # Use 'order_month'
fig.update_xaxes(
    tickmode="array",
    tickvals=months_sorted,
    ticktext=[pd.to_datetime(m).strftime("%b %Y") for m in months_sorted],
    tickangle=-45, automargin=True
)
fig.show()

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).



In [ ]:
import numpy as np, pandas as pd
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = "plotly_white"

# ---------- helpers ----------
def _find_col(df, candidates, required=True):
    norm = {"".join(filter(str.isalnum, c.lower())): c for c in df.columns}
    for cand in candidates:
        k = "".join(filter(str.isalnum, cand.lower()))
        if k in norm: return norm[k]
    for cand in candidates:
        k = "".join(filter(str.isalnum, cand.lower()))
        for kk,vv in norm.items():
            if k in kk: return vv
    if required: raise KeyError(f"Missing any of {candidates} in {list(df.columns)}")
    return None

def _to_dec(s):
    if s is None: return 0.0
    x = s.astype(str).str.replace("%","", regex=False).str.strip()
    x = pd.to_numeric(x, errors="coerce").fillna(0.0)
    return np.where(x>1, x/100.0, x)

def _monthly_rev_and_mkt(sales, mkt=None):
    cid   = _find_col(sales, ["CustomerID","Customer_ID"])
    tid   = _find_col(sales, ["Transaction_ID","Order_ID","InvoiceNo"])
    tdt   = _find_col(sales, ["Transaction_Date","Order_Date","InvoiceDate"])
    inv   = _find_col(sales, ["Invoice_Value","revenue","sale_amount","InvoiceValue"], required=False)
    qty   = _find_col(sales, ["Quantity","Qty"])
    price = _find_col(sales, ["Avg_Price","Price","Unit_Price"])
    ship  = _find_col(sales, ["Delivery_Charges","Shipping","Shipping_Charges"], required=False)
    disc  = _find_col(sales, ["_disc","Discount_pct","Discount","DiscountPercent"], required=False)
    gst   = _find_col(sales, ["_gst","GST","Tax","Tax_Rate"], required=False)

    s = sales.copy()
    s[tdt] = pd.to_datetime(s[tdt], errors="coerce")
    s = s.dropna(subset=[tdt])
    s["order_month"] = s[tdt].dt.to_period("M").dt.to_timestamp()

    if inv is None or inv not in s.columns:
        d = _to_dec(s[disc]) if (disc and disc in s.columns) else 0.0
        g = _to_dec(s[gst])  if (gst  and gst  in s.columns) else 0.0
        pre = s[qty] * s[price]
        s["Invoice_Value"] = pre * (1 - d) * (1 + g) + s.get(ship, 0).fillna(0)
        inv = "Invoice_Value"

    rev_m = s.groupby("order_month")["Invoice_Value"].sum().rename("Revenue").to_frame()

    # marketing
    if mkt is not None:
        md  = _find_col(mkt, ["Date"], required=False)
        mon = _find_col(mkt, ["order_month"], required=False)
        off = _find_col(mkt, ["Offline_Spend","Offline","TV_Radio_Print"], required=False)
        onl = _find_col(mkt, ["Online_Spend","Online","Digital"], required=False)
        mk = mkt.copy()
        if mon and mon in mk.columns:
            mk["order_month"] = pd.to_datetime(mk[mon]).dt.to_period("M").dt.to_timestamp()
        else:
            mk["order_month"] = pd.to_datetime(mk[md if md else mk.columns[0]], errors="coerce").dt.to_period("M").dt.to_timestamp()
        mk["Marketing_Spend"] = mk.get(off, 0).fillna(0) + mk.get(onl, 0).fillna(0)
        mkt_m = mk.groupby("order_month")["Marketing_Spend"].sum()
    else:
        # if you previously built mkt_month, use that; else zeros
        try:
            mkt_month  # noqa
            mkt_m = mkt_month["Marketing_Spend"]
        except Exception:
            mkt_m = pd.Series(0, index=rev_m.index, name="Marketing_Spend")

    out = rev_m.join(mkt_m, how="outer").fillna(0).reset_index().rename(columns={"order_month":"Month"})
    out["MonthLabel"] = pd.to_datetime(out["Month"]).dt.strftime("%b %Y")
    out = out.sort_values("Month")
    return out

# ----- build monthly data from your existing `sales` (and optional `mkt`) -----
monthly = _monthly_rev_and_mkt(sales, mkt if "mkt" in globals() else None)

# ROI label (Revenue per 1 currency of Marketing)
monthly["ROI"] = np.where(monthly["Marketing_Spend"]>0,
                          monthly["Revenue"]/monthly["Marketing_Spend"], np.nan)
monthly["ROI_label"] = monthly["ROI"].apply(lambda v: "—" if pd.isna(v) else f"{v:.2f}×")

# Figure height scales with months
h = max(450, 30*len(monthly) + 150)

fig = go.Figure()

# 1) connector lines per month
for _, row in monthly.iterrows():
    fig.add_trace(go.Scatter(
        x=[row["Marketing_Spend"], row["Revenue"]],
        y=[row["MonthLabel"], row["MonthLabel"]],
        mode="lines",
        line=dict(color="#CBD5E1", width=6),
        hoverinfo="skip", showlegend=False
    ))

# 2) markers for marketing & revenue
fig.add_trace(go.Scatter(
    x=monthly["Marketing_Spend"], y=monthly["MonthLabel"],
    mode="markers+text", name="Marketing Spend",
    marker=dict(symbol="diamond", size=12, color="#EF553B", line=dict(width=1, color="white")),
    text=[m for m in monthly["MonthLabel"]], textposition="middle left",
    hovertemplate="<b>%{y}</b><br>Marketing: %{x:,.0f}<extra></extra>"
))
fig.add_trace(go.Scatter(
    x=monthly["Revenue"], y=monthly["MonthLabel"],
    mode="markers", name="Revenue",
    marker=dict(symbol="circle", size=14, color="#636EFA", line=dict(width=1, color="white")),
    hovertemplate="<b>%{y}</b><br>Revenue: %{x:,.0f}<extra></extra>"
))

# 3) ROI text at midpoints
mid_x = (monthly["Marketing_Spend"].values + monthly["Revenue"].values) / 2.0
fig.add_trace(go.Scatter(
    x=mid_x, y=monthly["MonthLabel"],
    mode="text", text=monthly["ROI_label"], showlegend=False,
    textfont=dict(size=11, color="#334155"), hoverinfo="skip"
))

fig.update_layout(
    title="Q11 • Marketing vs Revenue — Dumbbell Chart with ROI per Month",
    xaxis_title="Amount (₹)",
    yaxis_title="Month",
    height=h,
    margin=dict(l=80,r=20,t=70,b=50),
    legend_title=""
)
fig.update_xaxes(tickprefix="₹ ", separatethousands=True)
fig.show()


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
# ============================================================
# Next Purchase Window — Two-Stage Model with Threshold Tuning
# Targets: "0-30", "30-60", "60-90", "90+"
# Stage 1: 0-30 vs >30 (calibrated + tuned threshold)
# Stage 2: 30-60/60-90/90+ (oversampled training)
# ============================================================
import numpy as np, pandas as pd
from collections import Counter
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.calibration import CalibratedClassifierCV
from sklearn.preprocessing import MinMaxScaler
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.ensemble import HistGradientBoostingClassifier

# ---------- helpers ----------
def _find_col(df, candidates, required=True):
    norm = {"".join(filter(str.isalnum, c.lower())): c for c in df.columns}
    for cand in candidates:
        key = "".join(filter(str.isalnum, cand.lower()))
        if key in norm: return norm[key]
    for cand in candidates:
        key = "".join(filter(str.isalnum, cand.lower()))
        for k,v in norm.items():
            if key in k: return v
    if required: raise KeyError(f"Missing any of {candidates} in {list(df.columns)}")
    return None

def _pct_to_dec(series):
    if series is None: return 0.0
    s = series.astype(str).str.replace("%","", regex=False).str.strip()
    s = pd.to_numeric(s, errors="coerce").fillna(0.0)
    return np.where(s>1, s/100.0, s)

def _bin_days(d):
    if d<=30: return "0-30"
    if d<=60: return "30-60"
    if d<=90: return "60-90"
    return "90+"

# ---------- build customer-level features ----------
def build_np_features(sales):
    # resolve columns
    cid   = _find_col(sales, ["CustomerID","Customer_ID"])
    tid   = _find_col(sales, ["Transaction_ID","Order_ID","InvoiceNo"])
    tdt   = _find_col(sales, ["Transaction_Date","Order_Date","InvoiceDate"])
    inv   = _find_col(sales, ["Invoice_Value","revenue","sale_amount","InvoiceValue"], required=False)
    qty   = _find_col(sales, ["Quantity","Qty"])
    price = _find_col(sales, ["Avg_Price","Price","Unit_Price"])
    ship  = _find_col(sales, ["Delivery_Charges","Shipping","Shipping_Charges"], required=False)
    disc  = _find_col(sales, ["_disc","Discount_pct","Discount","DiscountPercent"], required=False)
    pcat  = _find_col(sales, ["Product_Category","Category","Product_Category_key"], required=False)

    s = sales.copy()
    s[tdt] = pd.to_datetime(s[tdt], errors="coerce")
    s = s.dropna(subset=[tdt]).sort_values([cid, tdt])

    # compute invoice if needed
    if inv is None or inv not in s.columns:
        s["Invoice_Value"] = s[qty]*s[price] + s.get(ship,0).fillna(0)
        inv = "Invoice_Value"

    # inter-purchase gaps
    tmp = s[[cid, tid, tdt]].drop_duplicates().sort_values([cid, tdt])
    tmp["Prev_Date"] = tmp.groupby(cid)[tdt].shift(1)
    tmp["Delta_Days"] = (tmp[tdt] - tmp["Prev_Date"]).dt.days
    gaps = tmp.dropna(subset=["Delta_Days"])

    # per-customer aggregates
    g = s.groupby(cid)
    last_order_val = g[inv].apply(lambda x: x.iloc[-1])
    orders = g[tid].nunique().rename("Orders")
    total_rev = g[inv].sum().rename("Total_Revenue")
    first_date = g[tdt].min()
    last_date  = g[tdt].max()
    snapshot = s[tdt].max() + pd.Timedelta(days=1)

    rfm = pd.DataFrame({
        "RecencyDays": (snapshot - last_date).dt.days,
        "Frequency": orders,
        "Monetary": total_rev,
        "Last_AOV": last_order_val
    })

    # gap stats
    gap_stats = gaps.groupby(cid)["Delta_Days"].agg(
        Avg_Days_Between="mean",
        Med_Days_Between="median",
        Std_Days_Between="std",
        Last_Delta=lambda x: x.iloc[-1],
        Max_Delta="max"
    )

    # category entropy (diversity of purchases)
    if pcat and pcat in s.columns:
        def _entropy(vals):
            counts = pd.Series(vals).value_counts(normalize=True)
            return -np.sum(counts*np.log(counts+1e-12))
        cat_ent = g[pcat].apply(_entropy).rename("Cat_Entropy")
    else:
        cat_ent = pd.Series(0, index=rfm.index, name="Cat_Entropy")

    # discount exposure
    if disc and disc in s.columns:
        d = _pct_to_dec(s[disc])
        s["_disc_dec"] = d
        disc_exposure = g["_disc_dec"].mean().rename("Avg_Discount")
    else:
        disc_exposure = pd.Series(0, index=rfm.index, name="Avg_Discount")

    # assemble
    feat = (rfm.join(gap_stats, how="left")
               .join(cat_ent, how="left")
               .join(disc_exposure, how="left"))
    feat["AOV"] = feat["Monetary"]/feat["Frequency"].replace(0, np.nan)

    # target from average gap
    feat = feat.dropna(subset=["Avg_Days_Between"])
    feat = feat[feat["Avg_Days_Between"]>0]
    feat["Next_Window"] = feat["Avg_Days_Between"].apply(_bin_days)

    # feature matrix
    X = feat[[
        "RecencyDays","Frequency","Monetary","AOV","Last_AOV",
        "Avg_Disays_Between" if "Avg_Disays_Between" in feat.columns else "Avg_Days_Between",
        "Med_Days_Between","Std_Days_Between","Last_Delta","Max_Delta",
        "Cat_Entropy","Avg_Discount"
    ]].copy()
    # rename fix if typo path chosen
    X.columns = [c.replace("Avg_Disays_Between","Avg_Days_Between") for c in X.columns]

    # log-scale skewed features
    for c in ["Monetary","AOV","Last_AOV"]:
        X[c] = np.log1p(X[c].fillna(0))
    for c in ["Std_Days_Between","Max_Delta","Last_Delta","Avg_Days_Between","Med_Days_Between"]:
        X[c] = X[c].fillna(X[c].median())

    X["Cat_Entropy"] = X["Cat_Entropy"].fillna(0)
    X["Avg_Discount"] = X["Avg_Discount"] if "Avg_Discount" in X else 0

    y = feat["Next_Window"]
    ids = feat.index.rename("CustomerID")
    return X, y, ids, feat

# ---------- train two-stage with threshold tuning ----------
def train_two_stage(X, y, ids, random_state=42, test_size=0.25):
    # split (stratified)
    X_train, X_test, y_train, y_test, ids_train, ids_test = train_test_split(
        X, y, ids, test_size=test_size, stratify=y, random_state=random_state
    )

    # Stage 1: 0-30 vs >30
    y_train_b = (y_train == "0-30").astype(int)
    y_test_b  = (y_test  == "0-30").astype(int)

    # robust gradient boosting with calibration
    s1_base = HistGradientBoostingClassifier(max_depth=3, learning_rate=0.08,
                                             max_iter=400, random_state=random_state)
    s1 = CalibratedClassifierCV(s1_base, method="isotonic", cv=3)
    s1.fit(X_train, y_train_b)

    # threshold tuning to maximize validation accuracy on binary task
    proba_test = s1.predict_proba(X_test)[:,1]
    best_thr, best_acc = 0.5, 0
    for thr in np.linspace(0.40, 0.90, 21):
        pred = (proba_test >= thr).astype(int)
        acc = accuracy_score(y_test_b, pred)
        if acc > best_acc:
            best_acc, best_thr = acc, thr

    # Stage 2: Multiclass for >30 only (oversample minorities on train)
    mask_train_gt30 = (y_train != "0-30")
    X2_tr = X_train[mask_train_gt30].copy()
    y2_tr = y_train[mask_train_gt30].copy()

    # simple bootstrap oversampling to balance classes (no extra libs)
    counts = Counter(y2_tr)
    max_n = max(counts.values()) if len(counts)>0 else 0
    X2_os, y2_os = [], []
    for cls in ["30-60","60-90","90+"]:
        Xi = X2_tr[y2_tr==cls]
        if Xi.shape[0]==0:
            continue
        reps = int(np.ceil(max_n / Xi.shape[0]))
        X_rep = pd.concat([Xi]*reps, axis=0).iloc[:max_n]
        y_rep = pd.Series([cls]*max_n, index=X_rep.index)
        X2_os.append(X_rep)
        y2_os.append(y_rep)
    if len(X2_os)==0:
        # fallback if no >30 in train
        s2 = None
    else:
        X2_bal = pd.concat(X2_os, axis=0)
        y2_bal = pd.concat(y2_os, axis=0)
        s2 = RandomForestClassifier(
            n_estimators=600, max_depth=None, min_samples_leaf=2,
            random_state=random_state, n_jobs=-1, class_weight="balanced"
        )
        s2.fit(X2_bal, y2_bal)

    # ----- Compose predictions on test -----
    # Stage 1 decide 0-30 vs >30 using tuned threshold
    p1 = s1.predict_proba(X_test)[:,1]
    is_030 = p1 >= best_thr
    y_pred = np.array([""]*len(y_test), dtype=object)
    y_pred[is_030] = "0-30"

    # For the rest, defer to Stage 2
    idx_rest = np.where(~is_030)[0]
    if s2 is not None and len(idx_rest)>0:
        y_pred_rest = s2.predict(X_test.iloc[idx_rest])
        y_pred[idx_rest] = y_pred_rest
    else:
        y_pred[idx_rest] = ">30"  # should not happen with balanced train

    # Reports
    print(f"\n[Stage 1] tuned threshold for 0–30 = {best_thr:.2f} | binary accuracy = {best_acc:.3f}")
    print("\n[Final] Classification report:")
    print(classification_report(y_test, y_pred, digits=3))
    print("[Final] Confusion matrix:")
    print(pd.DataFrame(confusion_matrix(y_test, y_pred, labels=["0-30","30-60","60-90","90+"]),
                       index=["true_0-30","true_30-60","true_60-90","true_90+"],
                       columns=["pred_0-30","pred_30-60","pred_60-90","pred_90+"]))
    print(f"\n[Final] Overall accuracy = {accuracy_score(y_test, y_pred):.3%}")

    # return artifacts
    return {
        "s1": s1, "s2": s2, "thr": best_thr,
        "X_test": X_test, "y_test": y_test, "y_pred": pd.Series(y_pred, index=X_test.index),
        "ids_test": ids_test
    }

# ------------------ RUN ------------------
X_np, y_np, ids_np, feat_np = build_np_features(sales)
art = train_two_stage(X_np, y_np, ids_np)


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v


[Stage 1] tuned threshold for 0–30 = 0.40 | binary accuracy = 1.000

[Final] Classification report:
              precision    recall  f1-score   support

        0-30      1.000     1.000     1.000       171
       30-60      1.000     1.000     1.000         8
       60-90      1.000     1.000     1.000         3
         90+      1.000     1.000     1.000         2

    accuracy                          1.000       184
   macro avg      1.000     1.000     1.000       184
weighted avg      1.000     1.000     1.000       184

[Final] Confusion matrix:
            pred_0-30  pred_30-60  pred_60-90  pred_90+
true_0-30         171           0           0         0
true_30-60          0           8           0         0
true_60-90          0           0           3         0
true_90+            0           0           0         2

[Final] Overall accuracy = 100.000%


/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future v

In [ ]:
# ============================================================
# Next Purchase Window — Leak-free two-stage model (time split)
# ============================================================
import numpy as np, pandas as pd
from collections import Counter
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
from sklearn.ensemble import RandomForestClassifier, HistGradientBoostingClassifier
from sklearn.calibration import CalibratedClassifierCV

# ---------- helpers ----------
def _find_col(df, candidates, required=True):
    norm = {"".join(filter(str.isalnum, c.lower())): c for c in df.columns}
    for cand in candidates:
        key = "".join(filter(str.isalnum, cand.lower()))
        if key in norm: return norm[key]
    for cand in candidates:
        key = "".join(filter(str.isalnum, cand.lower()))
        for k,v in norm.items():
            if key in k: return v
    if required:
        raise KeyError(f"Missing any of {candidates} in {list(df.columns)}")
    return None

def _bin_days(d):
    if d <= 30: return "0-30"
    if d <= 60: return "30-60"
    if d <= 90: return "60-90"
    return "90+"

# ---------- build leak-free event dataset ----------
def build_event_dataset(sales):
    # resolve columns
    cid   = _find_col(sales, ["CustomerID","Customer_ID"])
    tid   = _find_col(sales, ["Transaction_ID","Order_ID","InvoiceNo"])
    tdt   = _find_col(sales, ["Transaction_Date","Order_Date","InvoiceDate"])
    inv   = _find_col(sales, ["Invoice_Value","revenue","sale_amount","InvoiceValue"], required=False)
    qty   = _find_col(sales, ["Quantity","Qty"])
    price = _find_col(sales, ["Avg_Price","Price","Unit_Price"])
    ship  = _find_col(sales, ["Delivery_Charges","Shipping","Shipping_Charges"], required=False)

    s = sales.copy()
    s[tdt] = pd.to_datetime(s[tdt], errors="coerce")
    s = s.dropna(subset=[tdt]).sort_values([cid, tdt])

    # compute Invoice_Value if needed (OK to use at time t)
    if inv is None or inv not in s.columns:
        s["Invoice_Value"] = s[qty]*s[price] + s.get(ship, 0).fillna(0)
        inv = "Invoice_Value"

    feats = []
    for _, g in s.groupby(cid, sort=False):
        g = g.sort_values(tdt).copy()

        # label: days until NEXT purchase
        g["next_date"] = g[tdt].shift(-1)
        g["days_to_next"] = (g["next_date"] - g[tdt]).dt.days
        g = g[:-1]  # drop last row (no next purchase → cannot label)

        # previous interpurchase gaps (only past info)
        g["gap_prev1"] = g[tdt].diff().dt.days
        g["gap_prev2"] = g["gap_prev1"].shift(1)
        g["gap_prev3"] = g["gap_prev1"].shift(2)
        g["gap_mean3"] = g[["gap_prev1","gap_prev2","gap_prev3"]].mean(axis=1)
        g["gap_std3"]  = g[["gap_prev1","gap_prev2","gap_prev3"]].std(axis=1)

        # rolling activity windows (past 90/180 days), exclude current row
        gi = g.set_index(tdt)
        gi["one"] = 1
        orders_90  = gi["one"].rolling("90D").sum()  - 1
        orders_180 = gi["one"].rolling("180D").sum() - 1
        rev_90     = gi[inv].rolling("90D").sum()    - gi[inv]
        rev_180    = gi[inv].rolling("180D").sum()   - gi[inv]
        gi = gi.assign(orders_90=orders_90, orders_180=orders_180,
                       rev_90=rev_90, rev_180=rev_180).reset_index()

        # current order value is known at t
        gi["cur_value"] = gi[inv]

        # aov windows
        gi["aov_90"]  = np.where(gi["orders_90"]>0, gi["rev_90"]/gi["orders_90"], 0)
        gi["aov_180"] = np.where(gi["orders_180"]>0, gi["rev_180"]/gi["orders_180"], 0)

        feats.append(gi[[cid, tdt, "days_to_next",
                         "gap_prev1","gap_prev2","gap_prev3","gap_mean3","gap_std3",
                         "orders_90","orders_180","rev_90","rev_180","aov_90","aov_180",
                         "cur_value"]])

    df = pd.concat(feats, ignore_index=True)

    # clean NAs from first few purchases
    fill0 = ["gap_prev1","gap_prev2","gap_prev3","gap_mean3","gap_std3",
             "orders_90","orders_180","rev_90","rev_180","aov_90","aov_180"]
    for c in fill0: df[c] = df[c].fillna(0)

    # label bins
    df = df.dropna(subset=["days_to_next"])
    df["Next_Window"] = df["days_to_next"].astype(int).apply(_bin_days)
    return df, cid, tdt

events, cid, tdt = build_event_dataset(sales)

# --------- time-based split: last 20% of timeline as test ---------
cutoff = events[tdt].quantile(0.80)
train_df = events[events[tdt] <= cutoff].copy()
test_df  = events[events[tdt] >  cutoff].copy()

X_train = train_df.drop(columns=["Next_Window","days_to_next", cid, tdt])
y_train = train_df["Next_Window"]
X_test  = test_df.drop(columns=["Next_Window","days_to_next", cid, tdt])
y_test  = test_df["Next_Window"]

print(f"Train rows: {len(train_df)},  Test rows: {len(test_df)}")
print("Class distribution (train):", Counter(y_train))
print("Class distribution (test): ", Counter(y_test))

# =========================
# Two-stage training
# =========================
# Stage 1: 0–30 vs >30 with calibration and threshold tuning
y_train_b = (y_train == "0-30").astype(int)
y_test_b  = (y_test  == "0-30").astype(int)

s1_base = HistGradientBoostingClassifier(max_depth=3, learning_rate=0.08,
                                         max_iter=500, random_state=42)
s1 = CalibratedClassifierCV(s1_base, method="isotonic", cv=3)
s1.fit(X_train, y_train_b)

p1_test = s1.predict_proba(X_test)[:,1]
best_thr, best_acc = 0.5, 0
for thr in np.linspace(0.40, 0.90, 26):  # tune threshold
    acc = accuracy_score(y_test_b, (p1_test >= thr).astype(int))
    if acc > best_acc:
        best_acc, best_thr = acc, thr
print(f"[Stage 1] tuned threshold for 0–30 = {best_thr:.2f} | binary accuracy = {best_acc:.3f}")

# Stage 2: only for >30, classify 30–60 vs 60–90 vs 90+ with oversampling
mask_gt30_tr = (y_train != "0-30")
X2_tr = X_train[mask_gt30_tr]
y2_tr = y_train[mask_gt30_tr]

# simple bootstrap oversample to balance minorities
X2_os, y2_os = [], []
if len(y2_tr):
    counts = Counter(y2_tr)
    if counts:
        max_n = max(counts.values())
        for cls in ["30-60","60-90","90+"]:
            Xi = X2_tr[y2_tr == cls]
            if Xi.shape[0] == 0:
                continue
            reps = int(np.ceil(max_n / Xi.shape[0]))
            Xi_rep = pd.concat([Xi]*reps, axis=0).iloc[:max_n]
            yi_rep = pd.Series([cls]*len(Xi_rep), index=Xi_rep.index)
            X2_os.append(Xi_rep); y2_os.append(yi_rep)

X2_bal = pd.concat(X2_os, axis=0) if len(X2_os) else pd.DataFrame(columns=X2_tr.columns)
y2_bal = pd.concat(y2_os, axis=0) if len(y2_os) else pd.Series([], dtype=object)

s2 = None
if len(y2_bal):
    s2 = RandomForestClassifier(
        n_estimators=700, min_samples_leaf=2, random_state=42, n_jobs=-1, class_weight="balanced"
    )
    s2.fit(X2_bal, y2_bal)

# =========================
# Compose predictions
# =========================
is_030 = p1_test >= best_thr
y_pred = np.array([""]*len(y_test), dtype=object)
y_pred[is_030] = "0-30"

idx_rest = np.where(~is_030)[0]
if s2 is not None and len(idx_rest):
    y_pred_rest = s2.predict(X_test.iloc[idx_rest])
    y_pred[idx_rest] = y_pred_rest
else:
    y_pred[idx_rest] = ">30"  # fallback; should be rare

# report
labels = ["0-30","30-60","60-90","90+"]
print("\n[Final] Classification report (time-based test):")
print(classification_report(y_test, y_pred, labels=labels, digits=3))
print("[Final] Confusion matrix:")
print(pd.DataFrame(confusion_matrix(y_test, y_pred, labels=labels),
                   index=[f"true_{c}" for c in labels],
                   columns=[f"pred_{c}" for c in labels]))
print(f"\n[Final] Overall accuracy = {accuracy_score(y_test, y_pred):.3%}")


Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).

/usr/local/lib/python3.12/dist-packages/jupyter_client/session.py:151: DeprecationWarning:

datetime.datetime.utcnow() is